#Pre Proccsing

Displaying the images:

In [6]:
from PIL import Image
import plotly.express as px

In [7]:
import numpy as np


In [8]:
def display_image(filename):
    img = Image.open(filename)
    # Convert the image to a NumPy array
    img_arr = np.array(img)

    # Display the image using Plotly Express
    fig = px.imshow(img_arr)
    fig.show()

In [10]:
display_image('img1_pts.jpg')

Retriving the first image's coordinates:





In [11]:
A_1 = np.array([493,487,1])
B_1 = np.array([132,444,1])
C_1 = np.array([724,619,1])
D_1 = np.array([966,553,1])
E_1 = np.array([751,505,1])
F_1 = np.array([770,485,1])
G_1 = np.array([847,452,1])
H_1 = np.array([582,539,1])
I_1 = np.array([518,417,1])

In [12]:
img1_lst=np.array([A_1,B_1,C_1,D_1,E_1,F_1,H_1]).T #list of seven correspondence points from image 1

In [13]:
display_image('img2_pts.jpg')

Retriving the second image's coordinates:



In [14]:
A_2 = np.array([444,327,1])
B_2 = np.array([416,258,1])
C_2 = np.array([159,371,1])
D_2 = np.array([228,416,1])
E_2 = np.array([352,364,1])
F_2 = np.array([540,402,1])
G_2 = np.array([716,430,1])
H_2 = np.array([361,360,1])
I_2 = np.array([547,290,1])

In [15]:
img2_lst=np.array([A_2,B_2,C_2,D_2,E_2,F_2,H_2]).T #list of seven correspondence points from image 2

In [16]:
display_image('img3_pts.jpg')

Retriving the third image's coordinates:

In [17]:
A_3 = np.array([599,411,1])
B_3 = np.array([888,357,1])
C_3 = np.array([433,348,1])
D_3 = np.array([277,364,1])
E_3 = np.array([388,380,1])
F_3 = np.array([320,462,1])
G_3 = np.array([134,504,1])
H_3 = np.array([511,399,1])
I_3 = np.array([614,407,1])

In [18]:
img3_lst=np.array([A_3,B_3,C_3,D_3,E_3,F_3,H_3]).T #list of seven correspondence points from image 3

#Building Trifocal Tensor and Retriving the epipols

In [2]:
import warnings


In [3]:
from numpy import *
import cv2

class Trifocal_Tensor:
    def __init__(self, *args):
        '''Initializing the Trifocal_Tensor with 3 sets of corresponding points
            (all 3xN).'''

        # checking the argumemts
        if len(args) == 3 and args[0].shape[0] == 3:
            self.T, self.scale = self.tensor_pts( *args )
        else:
            warnings.warn("Trifocal initialization failed!")

    def tensor_pts(self, x0, x1, x2):
        '''Calculates tensor from point correspondences.'''
        N = len(x0[0])
        M = zeros((N*4,27))
        for i in range(N):
            for j in range(3):
                block = zeros((4,9))
                block[[0,1,0,1,2,3,2,3,0,2,1,3,0,1,2,3],
                      [0,1,2,2,3,4,5,5,6,6,7,7,8,8,8,8]] = x0[j,i]
                      #+ and - according the epsilon notation
                block[:2,6:] *= -x1[0,i]
                block[2:,6:] *= -x1[1,i]
                block[:2,2] *= -x2[:2,i]
                block[2:,5] *= -x2[:2,i]
                block[:2,8] *= -x2[:2,i]
                block[2:,8] *= -x2[:2,i]
                M[i*4:i*4+4, j*9:j*9+9] = block.copy()
        # using SVD decomposition to find the trifocal tensor with least squares
        V = cv2.SVDecomp(M)[2]
        self.T = V[-1,:27].reshape((3,3,3))
        return self.T, 1.0



    def getEpipoles(self):
        '''Returns the epipole/position of camera 1 in image 2 and 3.'''

        # moving on each tensor matrix ,and calculates the left null vector of each matrix using SVD
        # afterwards, row - rise merging the results , creating a matrix of all left null vectors
        u = r_[[cv2.SVDecomp(t.T)[2][-1] for t in self.T]] #r_ :=  row-wise merging

        # using SVD to find the common perpendicuular to the left null vectors
        e_prime = cv2.SVDecomp(u)[2][-1]

        # same as before with transpose to find the common perpendicuular to the right null vectors
        v = r_[[cv2.SVDecomp(t)[2][-1] for t in self.T]]
        e_prime_prime = cv2.SVDecomp(v)[2][-1]
        return e_prime, e_prime_prime


In [19]:
tf = Trifocal_Tensor(img1_lst,img2_lst,img3_lst)

In [20]:
tf.tensor_pts(img1_lst,img2_lst,img3_lst)

(array([[[ 1.93650885e-05, -3.31714240e-05, -2.77164696e-08],
         [-1.00607210e-04,  5.19155159e-06, -1.71345871e-08],
         [-2.00163392e-07,  1.46248014e-07,  4.59305031e-10]],
 
        [[ 1.31980851e-03,  8.76707021e-04,  3.03149022e-06],
         [-1.01160115e-04, -4.03970858e-05,  1.47865513e-07],
         [ 4.21753688e-07,  2.91969836e-07,  1.84958802e-09]],
 
        [[-8.58005202e-01, -5.13272748e-01, -1.87417478e-03],
         [ 1.45499270e-02, -1.26576544e-02, -2.54235863e-04],
         [-2.71835784e-04, -2.41471291e-04, -1.55595477e-06]]]),
 1.0)

In [31]:
e_prime , e_prime_prime = tf.getEpipoles()

In [33]:
e_prime , e_prime_prime

(array([-0.291261, 0.956641, 0.002032]), array([0.232359, 0.161166, 0.000679]))

In [34]:
e_prime/=e_prime[2]  #normalization

In [35]:
e_prime

array([-143.341471, 470.801867, 1.000000])

In [36]:
e_prime_prime/=e_prime_prime[2] #normalization

In [37]:
e_prime_prime

array([342.207658, 237.357879, 1.000000])

In [38]:
np.set_printoptions(formatter={'float_kind':'{:f}'.format})

#The Results:

In [ ]:
print("e':" ,e_prime)
print("e'':" ,e_prime_prime)

e': [-143.341471 470.801867 1.000000]
e'': [342.207658 237.357879 1.000000]
